<a href="https://colab.research.google.com/github/unt-iialab/INFO5731_Spring2020/blob/master/Assignments/INFO5731_Assignment_Two.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [Apple iPhone 11](https://www.amazon.com/Apple-iPhone-11-64GB-Unlocked/dp/B07ZPKF8RG/ref=sr_1_13?dchild=1&keywords=iphone+12&qid=1631721363&sr=8-13) on amazon.

(2) Collect the top 10000 User Reviews of the film [Shang-Chi and the Legend of the Ten Rings](https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3) from IMDB.

(3) Collect all the reviews of the top 100 most popular software from [G2](https://www.g2.com/) or [Capterra](https://www.capterra.com/)

(4) Collect the abstracts of the top 10000 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(5) Collect all the information of the 904 narrators in the [Densho Digital Repository](https://ddr.densho.org/narrators/).

(6) Collect the top 10000 tweets by using hashtag ["#blacklivesmatter"](https://twitter.com/hashtag/blacklivesmatter) from Twitter. 


In [1]:
# import all the necessary moudles
import pandas as pd
import json
import urllib.request
from bs4 import BeautifulSoup
from urllib.request import urlopen
from selenium import webdriver 
from selenium.webdriver.common.by import By
import time
import warnings 
warnings.filterwarnings('ignore')
#define the url to extract reviews

url='https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3'

driver = webdriver.Chrome(executable_path='C:\chromedriver_win32\chromedriver.exe')

driver.get(url)

page = 1
#We want at least 10000 review, so get 50 at a safe number
while page<150:  
    try:
        #find the load more button on the webpage
        load_more = driver.find_element("id","load-more-trigger")
        #click on that button
        load_more.click()
        time.sleep(3)
        page+=1
    except:
        #If couldn't find any more button to click, stop
        break

#get a response and search for reviews
soup = BeautifulSoup(driver.page_source, features="html.parser")
reviews = soup.findAll('div', attrs={'class': 'text show-more__control'})

#get individual review in a list
listOfReviews = [review.get_text().replace('\n', "") for review in reviews]
#make a dataframe from list
df = pd.DataFrame({'User Reviews': listOfReviews})
#save the dataframe on a csv file
df.to_csv('user_Reviews.csv')

# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming. 

(6) Lemmatization.

In [1]:
# Importing Libraries
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import re
from nltk.stem import WordNetLemmatizer
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize

# Get all stopwords
stop_words = set(stopwords.words('english'))
# Read the dataset
df = pd.read_csv("user_Reviews.csv")

# lemmatization function
def lemmatization(string):
    #lemmatizer = WordNetLemmatizer()
    txt = [WordNetLemmatizer().lemmatize(x) for x in string]
    return txt

#stemming function
def stemming(string):
    txt = [PorterStemmer().stem(x) for x in string]
    return txt

# main function
def clean_text(dataframe, tt):
    # Remove the punctuations and noise
    dataframe[tt] = dataframe[tt].apply(lambda string: re.sub(r"(@[A-Za-z0-9]+)|([^0-9A-Za-z \t])|(\w+:\/\/\S+)|^rt|http.+?", "", string))
    # Remove the numbers
    dataframe[tt] = dataframe[tt].apply(lambda string: re.sub(r"\d+", "", string))
    # Remove the stopwords
    dataframe[tt] = dataframe[tt].apply(lambda string: ' '.join([w for w in string.split() if w not in (stop_words)]))
    # Convert to lower string
    dataframe[tt] = dataframe[tt].str.lower()
    # tokenize
    dataframe['tokens'] = dataframe[tt].apply(lambda x: word_tokenize(x))
    # Stemming and Lemmatization
    dataframe['tokens'].apply(lambda string: stemming(string))
    dataframe['tokens'].apply(lambda string: lemmatization(string))
    return dataframe

clean_text(df,"User Reviews")



Unnamed: 0                                       User Reviews  \
0             0  destin daniel crettons shangchi legend ten rin...   
1             1  everything comes beautiful science fiction bea...   
2             2  i big fan many many marvel films the reason i ...   
3             3  shangchi one marvel comics unknown underutiliz...   
4             4  shangchi boring film the characters okay story...   
..          ...                                                ...   
904         904  quite lot representation great trying expand m...   
905         905  shangchi legend ten rings superhero movie its ...   
906         906  i admit script pretty cheesy basic everything ...   
907         907  i impressed narrative film not predictable ama...   
908         908  i going much fate movie got proven wrong its s...   

                                                tokens  
0    [destin, daniel, crettons, shangchi, legend, t...  
1    [everything, comes, beautiful, science, fictio...  
2    [i, big, fan, many, many, marvel, films, the, ...  
3    [shangchi, one, marvel, comics, unknown, under...  
4    [shangchi, boring, film, the, characters, okay...  
..                                                 ...  
904  [quite, lot, representation, great, trying, ex...  
905  [shangchi, legend, ten, rings, superhero, movi...  
906  [i, admit, script, pretty, cheesy, basic, ever...  
907  [i, impressed, narrative, film, not, predictab...  
908  [i, going, much, fate, movie, got, proven, wro...  

[909 rows x 3 columns]

# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [2]:
# (1) Parts of Speech (POS) Tagging
from collections import Counter
import nltk

tokens = df['User Reviews'].apply(lambda x: word_tokenize(x))

for r in tokens:
    tags = nltk.pos_tag(r)
counts = Counter( tag for word,  tag in tags)
print(counts)

Counter({'NN': 23, 'JJ': 12, 'NNS': 7, 'RB': 5, 'VBP': 5, 'VB': 3, 'DT': 3, 'VBD': 2, 'MD': 2, 'VBG': 1, 'PRP$': 1, 'JJR': 1, 'JJS': 1, 'VBN': 1, 'IN': 1, 'VBZ': 1})


In [3]:
#(2) Constituency Parsing and Dependency Parsing:
# Constituency Parsing
grammar = "NP: {<DT>?<JJ>}"
cp  =nltk.RegexpParser(grammar)
for r in tokens:
    tags = nltk.pos_tag(r)
    result = cp.parse(tags)
    print(result)

(S
  destin/NN
  daniel/NN
  crettons/NNS
  shangchi/VBP
  legend/VBP
  (NP ten/JJ)
  rings/NNS
  marks/NNS
  bland/VBP
  start/VB
  (NP new/JJ)
  phase/NN
  marvel/NN
  (NP cinematic/JJ)
  universe/NN
  it/PRP
  spectacle/VBZ
  regards/NNS
  action/NN
  sequence/NN
  fighting/VBG
  choreography/NN
  film/NN
  misses/VBZ
  (NP solid/JJ)
  storyline/NN
  origin/NN
  story/NN
  (NP titular/JJ)
  character/NN
  lacks/VBZ
  personality/NN
  go/VBP
  (NP heroic/JJ)
  transformation/NN
  story/NN
  (NP arc/JJ)
  simu/NN
  liu/NN
  (NP strong/JJ)
  presence/NN
  shangchi/NN
  yet/RB
  overshadowed/VBN
  (NP many/JJ)
  (NP experienced/JJ)
  costars/NNS)
(S
  everything/NN
  comes/VBZ
  (NP beautiful/JJ)
  science/NN
  fiction/NN
  (NP beautiful/JJ)
  (NP mythical/JJ)
  creatures/NNS
  sometimes/RB
  creatures/NNS
  dont/VBP
  seem/VBP
  (NP real/JJ)
  seemed/VBD
  (NP real/JJ)
  well/RB
  done/VBN
  there/EX
  bit/NN
  (NP avatar/JJ)
  feeling/VBG
  fighting/VBG
  safekeeping/VBG
  peace/NN
  

In [5]:
# Dependency Parsing:
import stanza

# Download the language model
stanza.download('en')
sentences = df['User Reviews']
for sentence in sentences:

    # Build a Neural Pipeline
    nlp = stanza.Pipeline('en', processors = "tokenize,pos,lemma,depparse") 

    # Pass the sentence through the pipeline
    doc = nlp(sentence)

    # Print the dependencies of the first sentence in the doc object
    # Format - (Token, Index of head, Nature of dependency)
    # Index starts from 1, 0 is reserved for ROOT
    doc.sentences[0].print_dependencies()


    print ("{:<15} | {:<10} | {:<15} ".format('Token', 'Relation', 'Head'))
    print ("-" * 50)

    # Convert sentence object to dictionary  
    sent_dict = doc.sentences[0].to_dict()

    # iterate to print the token, relation and head
    for word in sent_dict:
      print ("{:<15} | {:<10} | {:<15} "
             .format(str(word['text']),str(word['deprel']), str(sent_dict[word['head']-1]['text'] if word['head'] > 0 else 'ROOT')))


2022-10-08 19:26:58 INFO: Downloading default packages for language: en (English) ...


2022-10-08 19:39:24 INFO: Finished downloading models and saved to C:\Users\sande\stanza_resources.
2022-10-08 19:39:24 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2022-10-08 19:39:25 WARNING: Can not find mwt: default from official model list. Ignoring it.
2022-10-08 19:39:25 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |
| depparse  | combined |

2022-10-08 19:39:25 INFO: Use device: cpu
2022-10-08 19:39:25 INFO: Loading: tokenize
2022-10-08 19:39:26 INFO: Loading: pos
2022-10-08 19:39:26 INFO: Loading: lemma
2022-10-08 19:39:26 INFO: Loading: depparse
2022-10-08 19:39:26 INFO: Done loading processors!
2022-10-08 19:39:28 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


('destin', 5, 'compound')
('daniel', 3, 'compound')
('crettons', 5, 'compound')
('shangchi', 5, 'compound')
('legend', 7, 'compound')
('ten', 7, 'nummod')
('rings', 8, 'nsubj')
('marks', 0, 'root')
('bland', 15, 'amod')
('start', 12, 'compound')
('new', 15, 'amod')
('phase', 15, 'compound')
('marvel', 15, 'compound')
('cinematic', 15, 'amod')
('universe', 8, 'obj')
('it', 20, 'nsubj')
('spectacle', 18, 'compound')
('regards', 20, 'compound')
('action', 20, 'compound')
('sequence', 24, 'nsubj')
('fighting', 20, 'acl')
('choreography', 23, 'compound')
('film', 24, 'nsubj')
('misses', 8, 'conj')
('solid', 28, 'amod')
('storyline', 27, 'compound')
('origin', 28, 'compound')
('story', 30, 'compound')
('titular', 30, 'amod')
('character', 31, 'nsubj')
('lacks', 24, 'conj')
('personality', 31, 'obj')
('go', 31, 'xcomp')
('heroic', 37, 'amod')
('transformation', 36, 'compound')
('story', 37, 'compound')
('arc', 33, 'obj')
('simu', 37, 'flat')
('liu', 38, 'flat')
('strong', 42, 'amod')
('presen

2022-10-08 19:39:28 WARNING: Can not find mwt: default from official model list. Ignoring it.
2022-10-08 19:39:29 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |
| depparse  | combined |

2022-10-08 19:39:29 INFO: Use device: cpu
2022-10-08 19:39:29 INFO: Loading: tokenize
2022-10-08 19:39:29 INFO: Loading: pos
2022-10-08 19:39:29 INFO: Loading: lemma
2022-10-08 19:39:29 INFO: Loading: depparse
2022-10-08 19:39:30 INFO: Done loading processors!
2022-10-08 19:39:31 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


...

('i', 2, 'nsubj')
('admit', 0, 'root')
('script', 2, 'obj')
('pretty', 5, 'advmod')
('cheesy', 7, 'amod')
('basic', 7, 'amod')
('everything', 2, 'obj')
('else', 7, 'amod')
('quite', 10, 'advmod')
('brilliant', 7, 'amod')
('beautiful', 7, 'amod')
('this', 15, 'det')
('coming', 15, 'amod')
('marvel', 15, 'compound')
('fan', 19, 'nsubj')
('the', 18, 'det')
('action', 18, 'compound')
('scenery', 19, 'nsubj')
('made', 2, 'parataxis')
('movie', 19, 'obj')
('not', 22, 'advmod')
('sure', 19, 'xcomp')
('awkwafina', 24, 'nsubj')
('invited', 22, 'ccomp')
('join', 24, 'xcomp')
('team', 27, 'compound')
('end', 29, 'compound')
('doesnt', 29, 'compound')
('skills', 25, 'obj')
Token           | Relation   | Head            
--------------------------------------------------
i               | nsubj      | admit           
admit           | root       | ROOT            
script          | obj        | admit           
pretty          | advmod     | cheesy          
cheesy          | amod       | everythi

2022-10-08 20:55:09 WARNING: Can not find mwt: default from official model list. Ignoring it.
2022-10-08 20:55:10 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |
| depparse  | combined |

2022-10-08 20:55:10 INFO: Use device: cpu
2022-10-08 20:55:10 INFO: Loading: tokenize
2022-10-08 20:55:10 INFO: Loading: pos
2022-10-08 20:55:11 INFO: Loading: lemma
2022-10-08 20:55:11 INFO: Loading: depparse
2022-10-08 20:55:12 INFO: Done loading processors!
2022-10-08 20:55:13 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


('i', 2, 'nsubj')
('impressed', 0, 'root')
('narrative', 4, 'amod')
('film', 2, 'obj')
('not', 9, 'advmod')
('predictable', 9, 'amod')
('amazing', 9, 'amod')
('fight', 9, 'compound')
('choreography', 4, 'conj')
('sometimes', 12, 'advmod')
('action', 12, 'compound')
('sequences', 2, 'parataxis')
('blurry', 14, 'amod')
('complaint', 2, 'conj')
('great', 18, 'amod')
('cast', 18, 'compound')
('color', 18, 'compound')
('grade', 2, 'parataxis')
('pretty', 20, 'advmod')
('good', 2, 'parataxis')
Token           | Relation   | Head            
--------------------------------------------------
i               | nsubj      | impressed       
impressed       | root       | ROOT            
narrative       | amod       | film            
film            | obj        | impressed       
not             | advmod     | choreography    
predictable     | amod       | choreography    
amazing         | amod       | choreography    
fight           | compound   | choreography    
choreography    | conj  

2022-10-08 20:55:14 WARNING: Can not find mwt: default from official model list. Ignoring it.
2022-10-08 20:55:15 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |
| depparse  | combined |

2022-10-08 20:55:15 INFO: Use device: cpu
2022-10-08 20:55:15 INFO: Loading: tokenize
2022-10-08 20:55:15 INFO: Loading: pos
2022-10-08 20:55:16 INFO: Loading: lemma
2022-10-08 20:55:16 INFO: Loading: depparse
2022-10-08 20:55:16 INFO: Done loading processors!


('i', 2, 'nsubj')
('going', 0, 'root')
('much', 5, 'amod')
('fate', 5, 'compound')
('movie', 2, 'obj')
('got', 7, 'aux:pass')
('proven', 2, 'ccomp')
('wrong', 7, 'xcomp')
('its', 10, 'nmod:poss')
('something', 7, 'obj')
('quite', 12, 'advmod')
('fresh', 14, 'amod')
('unexpected', 14, 'amod')
('scenes', 10, 'appos')
('first', 16, 'amod')
('minutes', 18, 'obl:tmod')
('bit', 18, 'obl:tmod')
('weak', 20, 'advmod')
('could', 20, 'aux')
('preformed', 7, 'conj')
('better', 23, 'amod')
('last', 23, 'amod')
('hour', 20, 'obl:tmod')
('absolute', 26, 'amod')
('best', 26, 'amod')
('couldve', 27, 'nsubj')
('gone', 2, 'parataxis')
('details', 29, 'compound')
('rings', 31, 'nsubj')
('might', 31, 'aux')
('want', 2, 'parataxis')
('rethink', 33, 'compound')
('cast', 31, 'obj')
('next', 35, 'amod')
('time', 31, 'obl:tmod')
('the', 38, 'det')
('music', 38, 'compound')
('hand', 39, 'nsubj')
('okay', 43, 'parataxis')
('final', 42, 'amod')
('battle', 42, 'compound')
('music', 43, 'nsubj')
('stood', 2, 'parat

In [8]:
# (3) Named Entity Recognition
import spacy
from spacy import displacy
from collections import Counter
import en_core_web_sm
nlp = en_core_web_sm.load()

for r in df['User Reviews']:
    doc = nlp(r)
    print([(X.text, X.label_) for X in doc.ents])
    print([(X, X.ent_iob_, X.ent_type_) for X in doc])

[('destin daniel', 'ORG')]
[(destin, 'B', 'ORG'), (daniel, 'I', 'ORG'), (crettons, 'O', ''), (shangchi, 'O', ''), (legend, 'O', ''), (ten, 'O', ''), (rings, 'O', ''), (marks, 'O', ''), (bland, 'O', ''), (start, 'O', ''), (new, 'O', ''), (phase, 'O', ''), (marvel, 'O', ''), (cinematic, 'O', ''), (universe, 'O', ''), (it, 'O', ''), (spectacle, 'O', ''), (regards, 'O', ''), (action, 'O', ''), (sequence, 'O', ''), (fighting, 'O', ''), (choreography, 'O', ''), (film, 'O', ''), (misses, 'O', ''), (solid, 'O', ''), (storyline, 'O', ''), (origin, 'O', ''), (story, 'O', ''), (titular, 'O', ''), (character, 'O', ''), (lacks, 'O', ''), (personality, 'O', ''), (go, 'O', ''), (heroic, 'O', ''), (transformation, 'O', ''), (story, 'O', ''), (arc, 'O', ''), (simu, 'O', ''), (liu, 'O', ''), (strong, 'O', ''), (presence, 'O', ''), (shangchi, 'O', ''), (yet, 'O', ''), (overshadowed, 'O', ''), (many, 'O', ''), (experienced, 'O', ''), (costars, 'O', '')]
[]
[(everything, 'O', ''), (comes, 'O', ''), (beauti

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 
##### Dependency parsing: 
By identifying each word as a node and showing relationships to its dependents, it defines the grammatical structure of a phrase. 
##### Constituency parsing: 
This parsing tree uses context-free grammar to show the syntactic structure of a sentence. as opposed to dependency parsing, which uses dependency grammar.